In [4]:
import numpy as np
import plotly.graph_objects as go

In [36]:
A = 2.5e-16 # Pa^-3/yr
AS = 1.8e-12 # Pa^-3/(m^2 yr)
N = 3
NP = 0.8
ICE_DENSITY = 910 # kg/m^3
GRAVITY = 9.8 # m/s^2
# KG = 1e-4 # 1e-2
KG = 3e-4
KD = 1e-1
RUNOFF_PCT = 0.5

# tuning params
M_FACTOR = 0.01
ANGLE = 5 # degrees
ELA = 2500 # m
UPLIFT = 5e-4 # m/yr
D_DIFF = 100 # m^2/yr
BASE = 2000 # m

NX = 200
dt = 1
TOTAL_YEARS = 100000
SAVE_INTERVAL = 1000  # how often to store snapshots for plotting

def create_mountain(angle, h0, base, n_points):
    """Create symmetric triangular mountain with an odd number of points."""
    # Ensure n_points is odd
    if n_points % 2 == 0:
        n_points += 1

    h0 = h0 - base

    angle_rad = np.radians(angle)
    half_base = h0 / np.tan(angle_rad)
    
    x_vals = np.linspace(0, 2 * half_base, n_points)
    bed = np.zeros(n_points)
    
    mid_point = n_points // 2  # exact center
    
    # Left side (ascending)
    for i in range(mid_point):
        bed[i] = (i / mid_point) * h0
    
    # Peak at midpoint
    bed[mid_point] = h0
    
    # Right side (descending)
    for i in range(mid_point + 1, n_points):
        bed[i] = ((n_points - 1 - i) / mid_point) * h0
    
    return x_vals, bed + base

def slope(surface, dx):
    """Calculate slope"""
    slope = np.zeros_like(surface)
    slope[1:-1] = (surface[2:] - surface[:-2]) / (2 * dx)
    slope[0] = (surface[1] - surface[0]) / dx
    slope[-1] = (surface[-1] - surface[-2]) / dx
    return slope

def flux_divergence(h, u, dx):
    flux = h * u
    divF = np.zeros_like(flux)

    # Compute divergence using central differences (interior points)
    divF[1:-1] = (flux[2:] - flux[:-2]) / (2 * dx)

    # Use one-sided differences at boundaries
    divF[0] = (flux[1] - flux[0]) / dx
    divF[-1] = (flux[-1] - flux[-2]) / dx

    return divF

def mass_balance(z, ela, m_factor):
    return np.minimum(m_factor * (z - ela), 0.1)

def sliding_velocity(h_ice, surf_slope):
    constant = 2 * AS * (ICE_DENSITY * GRAVITY * h_ice)**N / NP
    return -constant * np.abs(surf_slope)**(N-1) * surf_slope

def deformation_velocity(h_ice, surf_slope):
    constant = 2 * A * (ICE_DENSITY * GRAVITY)**N * h_ice**(N+1) / (N+2)
    return -constant * np.abs(surf_slope)**(N-1) * surf_slope

def calculate_erosion(us):
    return KG * np.abs(us)

def second_derivative(arr, dx):
    """Second derivative with central differences (Neumann BC: zero second derivative at edges)."""
    d2 = np.zeros_like(arr)
    d2[1:-1] = (arr[2:] - 2*arr[1:-1] + arr[:-2]) / (dx*dx)
    # simple one-sided at boundaries (could use ghost points or zero-gradient)
    d2[0] = (arr[2] - 2*arr[1] + arr[0]) / (dx*dx)
    d2[-1] = (arr[-1] - 2*arr[-2] + arr[-3]) / (dx*dx)
    return np.clip(d2, -1e2, 1e2)


def smoothing(arr, alpha, n_iter=1):
    """
    Smooths each side of a symmetric array independently, 
    keeping the central peak fixed.
    Assumes arr has an odd number of points.
    """
    out = arr.copy()
    n = len(arr)
    mid = n // 2  # middle index (peak)

    left = arr[:mid+1].copy()   # include midpoint in left side
    right = arr[mid:].copy()    # include midpoint in right side

    for _ in range(n_iter):
        # smooth left side (excluding leftmost and midpoint)
        left[1:mid] = left[1:-1] + alpha * (left[:-2] - 2 * left[1:-1] + left[2:])
        # smooth right side (excluding midpoint and rightmost)
        right[1:-1] = right[1:-1] + alpha * (right[:-2] - 2 * right[1:-1] + right[2:])

    # reconstruct: mirror around the center (shared midpoint)
    out[:mid+1] = left
    out[mid:] = right

    return out

def gaussian_kernel(sigma, truncate=3.0):
    if sigma <= 0:
        return np.array([1.0])
    # kernel radius in grid cells
    radius = int(np.ceil(truncate * sigma))
    x = np.arange(-radius, radius+1)
    k = np.exp(-(x**2) / (2.0 * sigma**2))
    k /= k.sum()
    return k

def gaussian_smooth(arr, sigma, truncate=3.0, mode='reflect'):
    """
    1D Gaussian smoothing via convolution (mass-conserving).
    mode: 'reflect'|'nearest'|'constant' etc. (we implement reflect/nearest)
    """
    k = gaussian_kernel(sigma, truncate)
    r = len(k)//2
    # pad arr
    if mode == 'reflect':
        pad = np.concatenate([arr[r:0:-1], arr, arr[-2:-r-2:-1]]) if r>0 else arr
    elif mode == 'nearest':
        pad = np.concatenate([np.full(r, arr[0]), arr, np.full(r, arr[-1])])
    else:
        # fallback to nearest
        pad = np.concatenate([np.full(r, arr[0]), arr, np.full(r, arr[-1])])
    # convolution (fast via np.convolve with 'valid' on padded array)
    sm = np.convolve(pad, k, mode='valid')
    return sm

In [37]:
# --- initialize domain ---
x, bed = create_mountain(ANGLE, ELA, BASE, NX)
bed_initial = bed.copy()  # store unmodified starting mountain profile
ice = np.zeros_like(bed)
dx = x[1] - x[0]
sed = np.zeros_like(bed)  # sediment thickness in each cell (m)
u_max = 0.49 * dx / dt

# Create a version of the mountain that only experiences uplift (no erosion/deposition)
bed_uplift_only = bed_initial.copy()

# storage for visualization
snapshots = []
years = []

# --- time evolution ---
for year in range(int(TOTAL_YEARS / dt)):
    surface = bed + sed + ice
    for _ in range(3):
        surface = gaussian_smooth(surface, sigma=0.5)
    surface_slope = np.clip(slope(surface, dx), -1e6, 1e6)
    d_mass_balance = mass_balance(surface, ELA, M_FACTOR)
    us = np.clip(sliding_velocity(ice, surface_slope) / np.sqrt(surface_slope**2 + 1), -u_max, u_max)
    ud = np.clip(deformation_velocity(ice, surface_slope) / np.sqrt(surface_slope**2 + 1), -u_max, u_max)
    erosion = calculate_erosion(us)

    # update
    lap_surf = second_derivative(ice + bed + sed, dx)
    ice += (d_mass_balance - flux_divergence(ice, us + ud, dx) + D_DIFF * lap_surf) * dt
    ice = np.clip(ice, 0, 1000)

    lap_sed = second_derivative(sed + bed, dx)
    deposition = KD * sed
    sed += ((1-RUNOFF_PCT) * erosion - flux_divergence(sed, us + ud, dx) - deposition + 1 * lap_sed) * dt
    sed = np.clip(sed, 0, 1e6)

    lap_bed = second_derivative(bed, dx)
    bed += (UPLIFT - erosion + deposition + 0.1 * lap_bed) * dt

    # uplift-only version (no erosion/deposition)
    bed_uplift_only += UPLIFT * dt

    # sed = gaussian_smooth(bed + sed, sigma=1.0) - bed
    # ice = gaussian_smooth(bed + sed + ice, sigma=1.0) - (bed + sed)
    # bed = gaussian_smooth(bed, sigma=0.1)

    # save for plotting
    if year % SAVE_INTERVAL == 0:
        snapshots.append((bed.copy(), ice.copy(), sed.copy(), bed_uplift_only.copy()))
        years.append(int(year * dt))

# --- create interactive Plotly animation ---
frames = []
baseline = np.min(snapshots[0][0]) - 50  # offset below lowest bed point

for i, (bed_i, ice_i, sed_i, bed_uplift_i) in enumerate(snapshots):
    y_bed = bed_i
    y_sed = bed_i + sed_i
    y_ice = y_sed + ice_i

    frames.append(go.Frame(
        data=[
            # Bedrock fill
            go.Scatter(
                x=np.concatenate([x, x[::-1]]),
                y=np.concatenate([baseline * np.ones_like(x), y_bed[::-1]]),
                fill='toself',
                fillcolor='saddlebrown',
                line=dict(color='saddlebrown'),
                name='Bedrock',
                hoverinfo='skip'
            ),
            # Sediment fill
            go.Scatter(
                x=np.concatenate([x, x[::-1]]),
                y=np.concatenate([y_bed, y_sed[::-1]]),
                fill='toself',
                fillcolor='gray',
                line=dict(color='gray'),
                name='Sediment',
                hoverinfo='skip'
            ),
            # Ice fill
            go.Scatter(
                x=np.concatenate([x, x[::-1]]),
                y=np.concatenate([y_sed, y_ice[::-1]]),
                fill='toself',
                fillcolor='skyblue',
                line=dict(color='skyblue'),
                name='Ice',
                hoverinfo='skip'
            ),
            # ELA line
            go.Scatter(
                x=x,
                y=np.full_like(x, ELA),
                mode='lines',
                line=dict(color='black', width=2, dash='dot'),
                name='ELA'
            ),
            # Original mountain with uplift only
            go.Scatter(
                x=x,
                y=bed_uplift_i,
                mode='lines',
                line=dict(color='black', width=2, dash='dash'),
                name='Uplift Only'
            )
        ],
        name=str(years[i])
    ))

# --- initial frame (year 0) ---
bed0, ice0, sed0, bed_uplift0 = snapshots[0]
y_bed0 = bed0
y_sed0 = bed0 + sed0
y_ice0 = y_sed0 + ice0

fig = go.Figure(
    data=[
        go.Scatter(
            x=np.concatenate([x, x[::-1]]),
            y=np.concatenate([baseline * np.ones_like(x), y_bed0[::-1]]),
            fill='toself',
            fillcolor='saddlebrown',
            line=dict(color='saddlebrown'),
            name='Bedrock'
        ),
        go.Scatter(
            x=np.concatenate([x, x[::-1]]),
            y=np.concatenate([y_bed0, y_sed0[::-1]]),
            fill='toself',
            fillcolor='gray',
            line=dict(color='gray'),
            name='Sediment'
        ),
        go.Scatter(
            x=np.concatenate([x, x[::-1]]),
            y=np.concatenate([y_sed0, y_ice0[::-1]]),
            fill='toself',
            fillcolor='skyblue',
            line=dict(color='skyblue'),
            name='Ice'
        ),
        # ELA line (dotted)
        go.Scatter(
            x=x,
            y=np.full_like(x, ELA),
            mode='lines',
            line=dict(color='black', width=2, dash='dot'),
            name='ELA'
        ),
        # Uplift-only mountain (dashed)
        go.Scatter(
            x=x,
            y=bed_uplift0,
            mode='lines',
            line=dict(color='black', width=2, dash='dash'),
            name='Uplift Only'
        )
    ],
    layout=go.Layout(
        title="Glacier–Mountain Evolution Over Time",
        xaxis=dict(title='Distance (m)'),
        yaxis=dict(title='Elevation (m)'),
        updatemenus=[{
            "buttons": [
                {"args": [None, {"frame": {"duration": 100, "redraw": True},
                                 "fromcurrent": True}],
                 "label": "Play", "method": "animate"},
                {"args": [[None], {"frame": {"duration": 0, "redraw": True},
                                   "mode": "immediate",
                                   "transition": {"duration": 0}}],
                 "label": "Pause", "method": "animate"}
            ],
            "direction": "left",
            "pad": {"r": 10, "t": 50},
            "type": "buttons",
            "x": 0.1, "xanchor": "right",
            "y": 0, "yanchor": "top"
        }],
        sliders=[{
            "steps": [
                {"args": [[str(years[i])],
                          {"frame": {"duration": 0, "redraw": True},
                           "mode": "immediate"}],
                 "label": f"{years[i]} yr", "method": "animate"}
                for i in range(len(years))
            ],
            "x": 0.1, "len": 0.9,
            "xanchor": "left",
            "y": -0.05, "yanchor": "top"
        }]
    ),
    frames=frames
)

fig.show()
